In [1]:
#First run this to load all modules and functions

import shutil
from datetime import datetime
from exif import Image
import os
import csv
import time
import geopandas as gpd
import fiona
from shapely.geometry import Point, Polygon
import pandas as pd
from csv import reader
fiona.drvsupport.supported_drivers['KML'] = 'rw'

def copy_found_images(images_found, path):
    for images in images_found:
        source = images[1]
        destination = images[0]+'\\'
        os.makedirs(os.path.dirname(destination), exist_ok=True)
        try:
            shutil.copy(source, destination)
            print('Image copied succesfully to: ', destination)
        except shutil.SameFileError:
            attempt=0
            while attempt <= 10:
                attempt +=1
                destination=destination+'-(same_name_'+str(attempt)+')'
            print("Source and destination represents the same file. Not copied: ", source)
        except:
            print("Error occurred while copying file. Not copied: ", source)        
  
def write_list_to_disk(raw_list, paths, file_name_prefix):
    for path in paths:
        if os.path.exists(path):
            sys_timestamp=time.time()
            file_name="%s-%s.csv" % (file_name_prefix, sys_timestamp)
            csv_file_name=os.path.join(path, file_name)
            with open(csv_file_name,"w", newline='') as csv_file:
                write = csv.writer(csv_file)
                write.writerows(raw_list)
            print("Image list sucessfully written to disk at %s" % csv_file_name)
        else:
            print("Path not accessible for writing" + path)

def write_master_to_disk(raw_list, paths, file_name):
    for path in paths:
        if os.path.exists(path):
            sys_timestamp=time.time()
            file_name="%s.csv" % (file_name)
            csv_file_name=os.path.join(path, file_name)
            with open(csv_file_name,"w", newline='') as csv_file:
                write = csv.writer(csv_file)
                write.writerows(raw_list)
            print("Image list sucessfully written to disk at %s" % csv_file)
        else:
            print("Path not accessible for writing" + path)
            
def find_any_image_files(root_paths):
    file_list=[]
    for root_path in root_paths:
        if os.path.exists(root_path):
            print("Root path is found: " + root_path)
            print('Busy looking for images')
            for (root,dirs,files) in os.walk(root_path, topdown=1): 
                for file in files:
                    if file.lower().endswith(('.png', '.jpg', '.jpeg')):
                        file_found_with_path=os.path.join(root, file)
                        file_list.append([file_found_with_path])
            print('Done')
        else:
            print("Root path is not found. Please check path accessibility: " + root_path)
    return(file_list)

def decimal_coords(coords, ref):
    decimal_degrees = coords[0] + coords[1] / 60 + coords[2] / 3600
    if ref == 'S' or ref == 'W':
        decimal_degrees = -decimal_degrees
    return decimal_degrees

def image_coordinates(image_list):
    GPS_list=[]
    for img_path in image_list:
        image_file=img_path[0]
        print(image_file)
        fail = 0
        try:
            with open(image_file, 'rb') as src:
                img = Image(src)
                date=('')
                coords=(0,0)
                if img.has_exif:
                    try:
                        date = img.datetime_original
                    except:
                        pass
                    try:
                        coords_lat = decimal_coords(img.gps_latitude,img.gps_latitude_ref)
                        coords_long = decimal_coords(img.gps_longitude,img.gps_longitude_ref)
                    except AttributeError:
                        print ('No Coordinates')
                        fail=1
                    if fail != 1:
                        GPS_list.append([src.name, date, coords_long, coords_lat])
                        print(f"Image {src.name}, Was taken: {img.datetime_original}, and has coordinates: {coords_lat}, {coords_long}")
                else:
                    print ('The Image has no EXIF information')
        except:
            print('Image not valid '+ image_file)
    return GPS_list

def find_images_in_kml(kml_file, csv_file):
    my_map = gpd.read_file(kml_file, driver='KML')
    print(my_map)
    image_found_list=[]
    last_found_photo = 0
    for i in range(0, len(my_map)):
        x=0
        folder = my_map.Name.loc[i]
        # open file in read mode
        with open(csv_file, 'r') as read_obj:
            # pass the file object to reader() to get the reader object
            csv_reader = reader(read_obj)
            # Iterate over each row in the csv using reader object
            for row in csv_reader:
                # row variable is a list that represents a row in csv
                p1=Point(float(row[2]),float(row[3]))
                check = my_map.contains(p1).values
                if check[i]==True:
                    datetime_taken = row[1]
                    date_time_obj=datetime.strptime(datetime_taken, '%Y:%m:%d %H:%M:%S')
                    date_str = date_time_obj.strftime("%Y-%m-%d")
                    directory = folder+"\\"+date_str
                    #print(directory,row[0])
                    image_found_list.append([directory,row[0]])
                    last_found_photo = date_time_obj.timestamp()
                else:
                    datetime_taken = row[1]
                    date_time_obj=datetime.strptime(datetime_taken, '%Y:%m:%d %H:%M:%S')
                    if abs(last_found_photo - date_time_obj.timestamp()) < 300:
                        date_str = date_time_obj.strftime("%Y-%m-%d")
                        directory = folder+"\\"+date_str
                        print(directory,row[0])
                        print(abs(last_found_photo - date_time_obj.timestamp()))
                        image_found_list.append([directory,row[0]])
    return(image_found_list)
  

In [2]:
#Start here to build a master file of all images and all images holding GPS coordinates

#Load the folders that need to be mined for images                    
#source_path_list=['C:\\Users\\cdego\\Pictures','Z:\\Carlos\\Photos']
#source_path_list=['C:\\Users\\Carlos de Gouveia\\Pictures\\iCloud Photos']
source_path_list=['D:\iOS_CdG']
#source_path_list=['Z:\\Isabel\\Photos']

#Specify destination folder for the results that follow
#master_path=['G:\\My Drive\\GPS_IMAGES_FOLDER']
master_path=['C:\\GPS_IMAGES_FOLDER']

#1
#Mine the source path for all images and put them into a list
all_images_found=find_any_image_files(source_path_list)                        

#Take the above list of images and save them to a CSV file in the destination folder. The CSV file is date stamped.
#This step creates a database of all images discovered which might be useful.
csv_file_prefix=('Image_List')
write_list_to_disk(all_images_found, master_path, csv_file_prefix)

#2
#Take the same list of images and use it to revisit the discovered images. This time
#interogate them for EXIF and GPS information. If GPS information is found, then
#put the image file into a list, together with Date and GPS information and then save it to a CSV file.
#Any previous CSV file with the same name is overwritten.
csv_file_name=('GPS_image_list_master')
images_with_GPS=image_coordinates(all_images_found)
write_master_to_disk(images_with_GPS, master_path, csv_file_name)

Root path is found: D:\iOS_CdG
Busy looking for images
Done
Image list sucessfully written to disk at C:\GPS_IMAGES_FOLDER\Image_List-1696594540.2320101.csv
D:\iOS_CdG\1684145475.297.JPG
Image D:\iOS_CdG\1684145475.297.JPG, Was taken: 2023:05:15 12:11:15, and has coordinates: -33.84232777777778, 18.64828333333333
D:\iOS_CdG\1684155527.537.JPG
Image D:\iOS_CdG\1684155527.537.JPG, Was taken: 2023:05:15 14:58:47, and has coordinates: -33.84249166666667, 18.648091666666666
D:\iOS_CdG\1216608967.000.JPG
No Coordinates
D:\iOS_CdG\1673621927.914.JPG
Image D:\iOS_CdG\1673621927.914.JPG, Was taken: 2023:01:13 16:58:47, and has coordinates: -33.88089444444444, 18.63326388888889
D:\iOS_CdG\1342000245.780.JPG
No Coordinates
D:\iOS_CdG\1673621930.305.JPG
Image D:\iOS_CdG\1673621930.305.JPG, Was taken: 2023:01:13 16:58:50, and has coordinates: -33.88082777777778, 18.633211111111113
D:\iOS_CdG\1673674228.051.JPG
Image D:\iOS_CdG\1673674228.051.JPG, Was taken: 2023:01:14 07:30:28, and has coordinates:

Image D:\iOS_CdG\1509266546.530.JPG, Was taken: 2017:10:29 10:42:26, and has coordinates: -33.92715, 18.413766666666664
D:\iOS_CdG\1509272165.919.JPG
Image D:\iOS_CdG\1509272165.919.JPG, Was taken: 2017:10:29 12:16:06, and has coordinates: -33.93223611111111, 18.406355555555553
D:\iOS_CdG\1509272170.289.JPG
Image D:\iOS_CdG\1509272170.289.JPG, Was taken: 2017:10:29 12:16:10, and has coordinates: -33.93223611111111, 18.406355555555553
D:\iOS_CdG\1509272174.694.JPG
Image D:\iOS_CdG\1509272174.694.JPG, Was taken: 2017:10:29 12:16:14, and has coordinates: -33.93223611111111, 18.406355555555553
D:\iOS_CdG\1509272184.970.JPG
Image D:\iOS_CdG\1509272184.970.JPG, Was taken: 2017:10:29 12:16:25, and has coordinates: -33.932288888888884, 18.406338888888886
D:\iOS_CdG\1509272189.674.JPG
Image D:\iOS_CdG\1509272189.674.JPG, Was taken: 2017:10:29 12:16:29, and has coordinates: -33.93228055555555, 18.406305555555555
D:\iOS_CdG\1509272205.322.JPG
Image D:\iOS_CdG\1509272205.322.JPG, Was taken: 2017:1

Image D:\iOS_CdG\1518972138.724.JPG, Was taken: 2018:02:18 18:42:18, and has coordinates: -34.02021111111111, 18.424875
D:\iOS_CdG\1518972143.659.JPG
Image D:\iOS_CdG\1518972143.659.JPG, Was taken: 2018:02:18 18:42:23, and has coordinates: -34.020224999999996, 18.424891666666667
D:\iOS_CdG\1673703930.843.JPG
Image D:\iOS_CdG\1673703930.843.JPG, Was taken: 2023:01:14 15:45:30, and has coordinates: -34.09097777777778, 18.485236111111114
D:\iOS_CdG\1520617738.832.JPG
Image D:\iOS_CdG\1520617738.832.JPG, Was taken: 2018:03:09 19:48:59, and has coordinates: -33.937691666666666, 18.399052777777776
D:\iOS_CdG\1520617780.942.JPG
Image D:\iOS_CdG\1520617780.942.JPG, Was taken: 2018:03:09 19:49:42, and has coordinates: -33.937663888888885, 18.399216666666668
D:\iOS_CdG\1520617782.802.JPG
Image D:\iOS_CdG\1520617782.802.JPG, Was taken: 2018:03:09 19:49:43, and has coordinates: -33.937663888888885, 18.399216666666668
D:\iOS_CdG\1520617999.719.JPG
Image D:\iOS_CdG\1520617999.719.JPG, Was taken: 201

Image D:\iOS_CdG\1523713202.146.JPG, Was taken: 2018:04:14 15:40:02, and has coordinates: -33.935805555555554, 18.40953888888889
D:\iOS_CdG\1523713298.352.JPG
Image D:\iOS_CdG\1523713298.352.JPG, Was taken: 2018:04:14 15:41:38, and has coordinates: -33.93535555555555, 18.40999722222222
D:\iOS_CdG\1523787142.737.JPG
Image D:\iOS_CdG\1523787142.737.JPG, Was taken: 2018:04:15 12:12:22, and has coordinates: -34.02003611111111, 18.48141944444444
D:\iOS_CdG\1523787145.670.JPG
Image D:\iOS_CdG\1523787145.670.JPG, Was taken: 2018:04:15 12:12:25, and has coordinates: -34.02036388888889, 18.481441666666665
D:\iOS_CdG\1523787148.303.JPG
Image D:\iOS_CdG\1523787148.303.JPG, Was taken: 2018:04:15 12:12:28, and has coordinates: -34.02032777777778, 18.48148611111111
D:\iOS_CdG\1523787213.839.JPG
Image D:\iOS_CdG\1523787213.839.JPG, Was taken: 2018:04:15 12:13:34, and has coordinates: -34.01976388888889, 18.481402777777777
D:\iOS_CdG\1523787214.973.JPG
Image D:\iOS_CdG\1523787214.973.JPG, Was taken: 2

Image D:\iOS_CdG\1526114508.793.JPG, Was taken: 2018:05:12 10:41:49, and has coordinates: -33.93216666666667, 18.406105555555555
D:\iOS_CdG\1526114509.460.JPG
Image D:\iOS_CdG\1526114509.460.JPG, Was taken: 2018:05:12 10:41:49, and has coordinates: -33.93216666666667, 18.406105555555555
D:\iOS_CdG\1526114510.027.JPG
Image D:\iOS_CdG\1526114510.027.JPG, Was taken: 2018:05:12 10:41:50, and has coordinates: -33.93216666666667, 18.406105555555555
D:\iOS_CdG\1526114511.028.JPG
Image D:\iOS_CdG\1526114511.028.JPG, Was taken: 2018:05:12 10:41:51, and has coordinates: -33.93216666666667, 18.406105555555555
D:\iOS_CdG\1526114511.495.JPG
Image D:\iOS_CdG\1526114511.495.JPG, Was taken: 2018:05:12 10:41:51, and has coordinates: -33.93216666666667, 18.406105555555555
D:\iOS_CdG\1526114511.995.JPG
Image D:\iOS_CdG\1526114511.995.JPG, Was taken: 2018:05:12 10:41:52, and has coordinates: -33.93216666666667, 18.406105555555555
D:\iOS_CdG\1526114512.562.JPG
Image D:\iOS_CdG\1526114512.562.JPG, Was taken

...

D:\iOS_CdG\1696321053.299.JPG
Image D:\iOS_CdG\1696321053.299.JPG, Was taken: 2023:10:03 10:17:33, and has coordinates: -34.034866666666666, 20.444769444444443
D:\iOS_CdG\1696321039.270.JPG
Image D:\iOS_CdG\1696321039.270.JPG, Was taken: 2023:10:03 10:17:19, and has coordinates: -34.034866666666666, 20.444769444444443
D:\iOS_CdG\1696321029.845.JPG
Image D:\iOS_CdG\1696321029.845.JPG, Was taken: 2023:10:03 10:17:09, and has coordinates: -34.03488888888889, 20.444777777777777
D:\iOS_CdG\1696321020.775.JPG
Image D:\iOS_CdG\1696321020.775.JPG, Was taken: 2023:10:03 10:17:00, and has coordinates: -34.03492222222222, 20.44468611111111
D:\iOS_CdG\1696321019.003.JPG
Image D:\iOS_CdG\1696321019.003.JPG, Was taken: 2023:10:03 10:16:59, and has coordinates: -34.03492222222222, 20.44468611111111
D:\iOS_CdG\1696321010.746.JPG
Image D:\iOS_CdG\1696321010.746.JPG, Was taken: 2023:10:03 10:16:50, and has coordinates: -34.034927777777774, 20.444675
D:\iOS_CdG\1696321004.355.JPG
Image D:\iOS_CdG\1696321

Image D:\iOS_CdG\1695823331.974.JPG, Was taken: 2023:09:27 16:02:11, and has coordinates: -34.09882777777778, 18.864147222222222
D:\iOS_CdG\1695823300.556.JPG
Image D:\iOS_CdG\1695823300.556.JPG, Was taken: 2023:09:27 16:01:40, and has coordinates: -34.098850000000006, 18.864211111111114
D:\iOS_CdG\1695823294.416.JPG
Image D:\iOS_CdG\1695823294.416.JPG, Was taken: 2023:09:27 16:01:34, and has coordinates: -34.098866666666666, 18.864180555555556
D:\iOS_CdG\1695823168.962.JPG
Image D:\iOS_CdG\1695823168.962.JPG, Was taken: 2023:09:27 15:59:28, and has coordinates: -34.09941944444445, 18.864116666666668
D:\iOS_CdG\1695823167.194.JPG
Image D:\iOS_CdG\1695823167.194.JPG, Was taken: 2023:09:27 15:59:27, and has coordinates: -34.09941944444445, 18.864116666666668
D:\iOS_CdG\1695823157.795.JPG
Image D:\iOS_CdG\1695823157.795.JPG, Was taken: 2023:09:27 15:59:17, and has coordinates: -34.099380555555555, 18.864158333333336
D:\iOS_CdG\1695822983.335.JPG
Image D:\iOS_CdG\1695822983.335.JPG, Was ta

Image D:\iOS_CdG\1695821512.170.JPG, Was taken: 2023:09:27 15:31:52, and has coordinates: -34.09976666666667, 18.862930555555558
D:\iOS_CdG\1695821440.191.JPG
Image D:\iOS_CdG\1695821440.191.JPG, Was taken: 2023:09:27 15:30:40, and has coordinates: -34.09970833333333, 18.86285
D:\iOS_CdG\1695821434.712.JPG
Image D:\iOS_CdG\1695821434.712.JPG, Was taken: 2023:09:27 15:30:34, and has coordinates: -34.099694444444445, 18.862861111111112
D:\iOS_CdG\1695821276.203.JPG
Image D:\iOS_CdG\1695821276.203.JPG, Was taken: 2023:09:27 15:27:56, and has coordinates: -34.10016388888889, 18.863544444444447
D:\iOS_CdG\1695821167.596.JPG
Image D:\iOS_CdG\1695821167.596.JPG, Was taken: 2023:09:27 15:26:07, and has coordinates: -34.100833333333334, 18.86460277777778
D:\iOS_CdG\1695821152.173.JPG
Image D:\iOS_CdG\1695821152.173.JPG, Was taken: 2023:09:27 15:25:52, and has coordinates: -34.10076111111111, 18.86447777777778
D:\iOS_CdG\1695821128.048.JPG
Image D:\iOS_CdG\1695821128.048.JPG, Was taken: 2023:09:

Image D:\iOS_CdG\1695818871.973.JPG, Was taken: 2023:09:27 14:47:51, and has coordinates: -34.100116666666665, 18.865586111111114
D:\iOS_CdG\1695818815.496.JPG
Image D:\iOS_CdG\1695818815.496.JPG, Was taken: 2023:09:27 14:46:55, and has coordinates: -34.10031388888889, 18.865669444444446
D:\iOS_CdG\1695818807.731.JPG
Image D:\iOS_CdG\1695818807.731.JPG, Was taken: 2023:09:27 14:46:47, and has coordinates: -34.10030833333334, 18.865597222222224
D:\iOS_CdG\1695818677.739.JPG
Image D:\iOS_CdG\1695818677.739.JPG, Was taken: 2023:09:27 14:44:37, and has coordinates: -34.10030833333334, 18.865586111111114
D:\iOS_CdG\1695818593.380.JPG
Image D:\iOS_CdG\1695818593.380.JPG, Was taken: 2023:09:27 14:43:13, and has coordinates: -34.10035833333333, 18.865575
D:\iOS_CdG\1695818590.985.JPG
Image D:\iOS_CdG\1695818590.985.JPG, Was taken: 2023:09:27 14:43:10, and has coordinates: -34.10035833333333, 18.865575
D:\iOS_CdG\1695818588.044.JPG
Image D:\iOS_CdG\1695818588.044.JPG, Was taken: 2023:09:27 14:4

D:\iOS_CdG\1696498032.384.JPG
Image D:\iOS_CdG\1696498032.384.JPG, Was taken: 2023:10:05 11:27:12, and has coordinates: -33.92248055555555, 18.857344444444447
D:\iOS_CdG\1696498030.603.JPG
Image D:\iOS_CdG\1696498030.603.JPG, Was taken: 2023:10:05 11:27:10, and has coordinates: -33.92249722222222, 18.857325000000003
D:\iOS_CdG\1696498029.217.JPG
Image D:\iOS_CdG\1696498029.217.JPG, Was taken: 2023:10:05 11:27:09, and has coordinates: -33.92255833333333, 18.857155555555558
Image list sucessfully written to disk at <_io.TextIOWrapper name='C:\\GPS_IMAGES_FOLDER\\GPS_image_list_master.csv' mode='w' encoding='cp1252'>


In [3]:
#Use this to locate images within the KML polygons.
#The images will be collected from the source destinations (make sure
#the destination folders are accessible) and copied to the destination folder.

#Specify the KML file
#kml_file='G:\\My Drive\\GPS_IMAGES_FOLDER\\Untitled Project (6).kml'
#kml_file='G:\\My Drive\\GPS_IMAGES_FOLDER\\Untitled Project (6).kml'
kml_file='C:\\GPS_IMAGES_FOLDER\\DVM Projects.kml'

#Specify the CSV file containing the image list and the respective GPS coordinates.
#Make sure the CSV names corresponds with the file name specified during the master file creation process
#csv_file='G:\\My Drive\\GPS_IMAGES_FOLDER\\GPS_image_list_master.csv'
csv_file='C:\\GPS_IMAGES_FOLDER\\GPS_image_list_master.csv'

#Specify destination folder where the selected images will be copied to
#destination_folder=('G:\\My Drive\\GPS_IMAGES_FOLDER')
destination_folder=('C:\\GPS_IMAGES_FOLDER')

#Sift through the list of GPS coordinates. If an image falls within a KML
#polygon, then put it into a list.
qualifying_image_list=find_images_in_kml(kml_file, csv_file)

#Take the list and use it to copy the qualifying images to their respective folders.
#The folders names coorespond with the polygon names created with GOOGLE Earth.
#The KML file can hold several polygons. Each polygon must have a unique name.
copy_found_images(qualifying_image_list, "")

                                                 Name  \
0   C:\Users\Carlos de Gouveia\My Drive\Projects\E...   
1   C:\Users\Carlos de Gouveia\My Drive\Projects\E...   
2   C:\Users\Carlos de Gouveia\My Drive\Projects\E...   
3   C:\Users\Carlos de Gouveia\My Drive\Projects\R...   
4   C:\Users\Carlos de Gouveia\My Drive\Projects\E...   
5   C:\Users\Carlos de Gouveia\My Drive\Projects\E...   
6   C:\Users\Carlos de Gouveia\My Drive\Projects\E...   
7   C:\Users\Carlos de Gouveia\My Drive\Projects\E...   
8   C:\Users\Carlos de Gouveia\My Drive\Projects\E...   
9   C:\Users\Carlos de Gouveia\My Drive\Projects\E...   
10  C:\Users\Carlos de Gouveia\My Drive\Projects\E...   
11  C:\Users\Carlos de Gouveia\My Drive\Projects\E...   
12  C:\Users\Carlos de Gouveia\My Drive\Projects\E...   
13  C:\Users\Carlos de Gouveia\My Drive\Projects\C...   
14  C:\Users\Carlos de Gouveia\My Drive\Projects\E...   
15  C:\Users\Carlos de Gouveia\My Drive\Projects\E...   

                        Descri

C:\Users\Carlos de Gouveia\My Drive\Projects\E5186 - US, Coetzenberg Centre Upgrade - GA\Photos\2023-06-14 D:\iOS_CdG\1686749699.015.JPG
111.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2018-12-07 D:\iOS_CdG\1544183654.630.JPG
85.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2019-02-20 D:\iOS_CdG\1550667824.993.JPG
12.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2019-02-20 D:\iOS_CdG\1550667907.494.JPG
94.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2019-03-22 D:\iOS_CdG\1553258721.120.JPG
40.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2019-03-22 D:\iOS_CdG\1553258812.999.JPG
132.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2019-03-22 D:\iOS_CdG\1553258883.629.JPG
203.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2019-03-22 D:\iOS_CdG\1553258943.218.JPG
262.0
C:\Users\Carlo

C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2022-11-14 D:\iOS_CdG\1668420324.059.JPG
177.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2022-11-14 D:\iOS_CdG\1668420339.774.JPG
193.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2022-11-14 D:\iOS_CdG\1668423569.000.JPG
3.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2022-11-14 D:\iOS_CdG\1668426474.506.JPG
17.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2022-11-14 D:\iOS_CdG\1668426586.074.JPG
19.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2022-11-16 D:\iOS_CdG\1668597966.830.JPG
7.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2022-11-16 D:\iOS_CdG\1668597970.860.JPG
11.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2022-11-16 D:\iOS_CdG\1668597981.319.JPG
22.0
C:\Users\Carlos de Gouveia\My Drive\Proj

C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-02-13 D:\iOS_CdG\1676280264.575.JPG
30.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-02-13 D:\iOS_CdG\1676280488.989.JPG
40.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-02-13 D:\iOS_CdG\1676280497.613.JPG
49.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-02-13 D:\iOS_CdG\1676281145.478.JPG
13.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-02-13 D:\iOS_CdG\1676281151.332.JPG
19.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-02-13 D:\iOS_CdG\1676281153.568.JPG
21.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-02-13 D:\iOS_CdG\1676281339.896.JPG
8.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-02-13 D:\iOS_CdG\1676281400.262.JPG
12.0
C:\Users\Carlos de Gouveia\My Drive\Proje

C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-04-17 D:\iOS_CdG\1681735933.390.JPG
57.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-04-17 D:\iOS_CdG\1681736402.296.JPG
23.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-04-17 D:\iOS_CdG\1681736426.893.JPG
47.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-04-17 D:\iOS_CdG\1681736479.662.JPG
100.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-04-26 D:\iOS_CdG\1682505340.137.JPG
20.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-04-26 D:\iOS_CdG\1682505358.624.JPG
38.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-04-26 D:\iOS_CdG\1682505398.619.JPG
78.0
C:\Users\Carlos de Gouveia\My Drive\Projects\E5158 - Polymer (CdG)\Photos\2023-05-08 D:\iOS_CdG\1683544421.896.JPG
4.0
C:\Users\Carlos de Gouveia\My Drive\Proj

...

Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-08-21\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-08-21\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-08-21\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-08-21\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-08-21\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-08-21\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-08-21\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-08-21\
Image co

Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image co

Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E4885 Dalevale Clinic - (CdG)\Photos\2023-09-15\
Image co

Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de

Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de Gouveia\My Drive\Projects\E5069 - Grabouw Clinic\Pictures\2023-09-07\
Image copied succesfully to:  C:\Users\Carlos de